# Pré-processamento dos Dados do CPGF

**Projeto:** Detecção de Anomalias no Uso do Cartão de Pagamento do Governo Federal  
**Disciplina:** Mineração de Dados  
**Etapa:** 1.Pré-processamento

---

## 0. Configuração do Ambiente

Montagem do ambiente para instalação de dependências e importação das bibliotecas necessárias.

In [3]:
!pip install pandas matplotlib seaborn scikit-learn plotly

Defaulting to user installation because normal site-packages is not writeable



[notice] A new release of pip is available: 25.3 -> 26.0.1
[notice] To update, run: C:\Users\didatikos\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.13_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [4]:
!pip install -r ../requirements.txt

Defaulting to user installation because normal site-packages is not writeable
  Using cached openpyxl-3.1.5-py2.py3-none-any.whl.metadata (2.5 kB)
  Using cached jupyter-1.1.1-py2.py3-none-any.whl.metadata (2.0 kB)
  Using cached et_xmlfile-2.0.0-py3-none-any.whl.metadata (2.7 kB)
  Using cached notebook-7.5.4-py3-none-any.whl.metadata (10 kB)
  Using cached jupyter_console-6.6.3-py3-none-any.whl.metadata (5.8 kB)
  Using cached nbconvert-7.17.0-py3-none-any.whl.metadata (8.4 kB)
  Using cached ipywidgets-8.1.8-py3-none-any.whl.metadata (2.4 kB)
  Using cached jupyterlab-4.5.5-py3-none-any.whl.metadata (16 kB)
  Using cached widgetsnbextension-4.0.15-py3-none-any.whl.metadata (1.6 kB)
  Using cached jupyterlab_widgets-3.0.16-py3-none-any.whl.metadata (20 kB)
  Using cached async_lru-2.2.0-py3-none-any.whl.metadata (7.2 kB)
  Using cached httpx-0.28.1-py3-none-any.whl.metadata (7.1 kB)
  Using cached jinja2-3.1.6-py3-none-any.whl.metadata (2.9 kB)
  Using cached jupyter_lsp-2.3.0-py3-no


[notice] A new release of pip is available: 25.3 -> 26.0.1
[notice] To update, run: C:\Users\didatikos\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.13_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


## 1. Carregamento dos Dados

Leitura dos arquivos CSV do CPGF (a partir de 2022) com link disponível na pasta `dados/`.

> O link é um redirecionamento para o Drive com 36 datasets.

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
import glob
import warnings
import plotly.express as px
from sklearn.preprocessing import StandardScaler
import numpy as np
from scipy.stats import norm


warnings.filterwarnings('ignore')
sns.set_theme(style='whitegrid', palette='muted')
plt.rcParams['figure.figsize'] = (12, 6)


print('Bibliotecas carregadas com sucesso.')

Bibliotecas carregadas com sucesso.


In [4]:
csv_files = sorted(glob.glob(os.path.join("../datasets", '*.csv')))
print(f'Arquivos encontrados: {len(csv_files)}')

aux=0
dfs = []

for f in csv_files:
    df_temp = pd.read_csv(f, sep=';', encoding='latin-1', decimal = ',')
    dfs.append(df_temp)
    aux+=1
    if aux <= 3:
        print(f'  - {os.path.basename(f)}')
    elif aux == 3:    
        print("  - ...")

df = pd.concat(dfs, ignore_index=True)

print(f'\nTotal de registros carregados: {df.shape[0]:,}')

print(f'Total de colunas: {df.shape[1]} \n')

print(f'Nomes das Colunas: {df.columns}')

Arquivos encontrados: 36
  - 202201_CPGF.csv
  - 202202_CPGF.csv
  - 202203_CPGF.csv

Total de registros carregados: 411,652
Total de colunas: 15 

Nomes das Colunas: Index(['CÓDIGO ÓRGÃO SUPERIOR', 'NOME ÓRGÃO SUPERIOR', 'CÓDIGO ÓRGÃO',
       'NOME ÓRGÃO', 'CÓDIGO UNIDADE GESTORA', 'NOME UNIDADE GESTORA',
       'ANO EXTRATO', 'MÊS EXTRATO', 'CPF PORTADOR', 'NOME PORTADOR',
       'CNPJ OU CPF FAVORECIDO', 'NOME FAVORECIDO', 'TRANSAÇÃO',
       'DATA TRANSAÇÃO', 'VALOR TRANSAÇÃO'],
      dtype='str')


---

## 2. Exploração dos Dados
### 2.1 Fundamentação Teórica

Utilizamos as seguintes técnicas e ferramentas:
- altermanos a coluna VALOR TRANSAÇÃO para float.

- Estatísticas resumidas (média, mediana, desvio padrão, quartis);
- Visualizações gráficas  (boxplot nessa etapa)  para identificar
  distribuições, padrões e possíveis anomalias visuais nos atributos.

Essa parte foi necessaria antes de aplicar qualquer técnica de mineração 

| Campo                     | Descrição resumida |
|---------------------------|--------------------|
| Código Órgão Superior     | Identificador do órgão superior responsável pelo cartão. |
| Nome Órgão Superior       | Nome do órgão superior da unidade gestora. |
| Código Órgão Subordinado  | Identificador do órgão subordinado ao órgão superior. |
| Nome Órgão Subordinado    | Nome do órgão subordinado da unidade gestora. |
| Código Unidade Gestora    | Código da unidade responsável pela gestão do recurso. |
| Nome Unidade Gestora      | Nome da unidade gestora. |
| Ano Extrato               | Ano em que ocorreu a transação. |
| Mês Extrato               | Mês em que ocorreu a transação. |
| CPF Portador              | CPF do portador do cartão que realizou a transação. |
| Nome Portador             | Nome do portador do cartão. |
| Transação                 | Tipo de operação realizada com o cartão (compra, saque, etc.). |
| Data Transação            | Data em que a transação foi efetuada. |
| CNPJ ou CPF do Favorecido | Documento de quem recebeu o pagamento. |
| Nome Favorecido           | Nome do estabelecimento ou pessoa que recebeu o valor. |
| Valor Transação           | Valor monetário da transação realizada. |

In [6]:
df.info()

<class 'pandas.DataFrame'>
RangeIndex: 411652 entries, 0 to 411651
Data columns (total 15 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   CÓDIGO ÓRGÃO SUPERIOR   411652 non-null  int64  
 1   NOME ÓRGÃO SUPERIOR     411652 non-null  str    
 2   CÓDIGO ÓRGÃO            411652 non-null  int64  
 3   NOME ÓRGÃO              411652 non-null  str    
 4   CÓDIGO UNIDADE GESTORA  411652 non-null  int64  
 5   NOME UNIDADE GESTORA    411652 non-null  str    
 6   ANO EXTRATO             411652 non-null  int64  
 7   MÊS EXTRATO             411652 non-null  int64  
 8   CPF PORTADOR            312122 non-null  str    
 9   NOME PORTADOR           411652 non-null  str    
 10  CNPJ OU CPF FAVORECIDO  411652 non-null  int64  
 11  NOME FAVORECIDO         411652 non-null  str    
 12  TRANSAÇÃO               411652 non-null  str    
 13  DATA TRANSAÇÃO          312122 non-null  str    
 14  VALOR TRANSAÇÃO         411652 

In [44]:
df['DATA TRANSAÇÃO'] = pd.to_datetime(df['DATA TRANSAÇÃO'], errors='coerce')

In [45]:
df['DATA TRANSAÇÃO'].head()


0   2021-08-12
1   2021-01-12
2          NaT
3   2021-06-12
4          NaT
Name: DATA TRANSAÇÃO, dtype: datetime64[us]

In [51]:
# str-> datetime aaaa-mm-dd
df['DATA TRANSAÇÃO'] = pd.to_datetime(
    df['DATA TRANSAÇÃO'],
    format='%d/%m/%Y'
)

In [55]:
df['DATA TRANSAÇÃO'].head()


0   2021-08-12
1   2021-01-12
2          NaT
3   2021-06-12
4          NaT
Name: DATA TRANSAÇÃO, dtype: datetime64[us]

In [56]:
df['DATA TRANSAÇÃO'].head()

0   2021-08-12
1   2021-01-12
2          NaT
3   2021-06-12
4          NaT
Name: DATA TRANSAÇÃO, dtype: datetime64[us]

In [7]:
# --- 2.2 Visão geral do DataFrame ---
print(' Primeiras linhas ')
display(df.head())

print('\n Informações gerais')
df.info()

print('\n Tipos de dados ')
display(df.dtypes)


 Primeiras linhas 


CÓDIGO ÓRGÃO SUPERIOR       NOME ÓRGÃO SUPERIOR  CÓDIGO ÓRGÃO  \
0                  63000  Advocacia-Geral da União         63000   
1                  63000  Advocacia-Geral da União         63000   
2                  63000  Advocacia-Geral da União         63000   
3                  63000  Advocacia-Geral da União         63000   
4                  63000  Advocacia-Geral da União         63000   

                                          NOME ÓRGÃO  CÓDIGO UNIDADE GESTORA  \
0  Advocacia-Geral da União - Unidades com víncul...                  110161   
1  Advocacia-Geral da União - Unidades com víncul...                  110161   
2  Advocacia-Geral da União - Unidades com víncul...                  110161   
3  Advocacia-Geral da União - Unidades com víncul...                  110161   
4  Advocacia-Geral da União - Unidades com víncul...                  110161   

                           NOME UNIDADE GESTORA  ANO EXTRATO  MÊS EXTRATO  \
0  SUPERINTENDENCIA REG. DE ADMIN. DA 1ª REGIAO         2022            1   
1  SUPERINTENDENCIA REG. DE ADMIN. DA 1ª REGIAO         2022            1   
2  SUPERINTENDENCIA REG. DE ADMIN. DA 1ª REGIAO         2022            1   
3  SUPERINTENDENCIA REG. DE ADMIN. DA 1ª REGIAO         2022            1   
4  SUPERINTENDENCIA REG. DE ADMIN. DA 1ª REGIAO         2022            1   

     CPF PORTADOR                      NOME PORTADOR  CNPJ OU CPF FAVORECIDO  \
0  ***.177.590-**         EDSON LUIS GARCIA FAGUNDES           1368970000107   
1  ***.725.752-**                VIVIANE CORREA LIMA          84646934000195   
2  ***.384.652-**  CARLOS EPAMINONDAS GOMES DA SILVA           5452754000104   
3  ***.177.590-**         EDSON LUIS GARCIA FAGUNDES                      -2   
4  ***.177.590-**         EDSON LUIS GARCIA FAGUNDES                      -2   

                                     NOME FAVORECIDO                TRANSAÇÃO  \
0                                 RANZAN & GRAF LTDA  COMPRA A/V - R$ - APRES   
1  PORTOSOFT COMERCIO DE PRODUTOS DE INFORMATICA ...  COMPRA A/V - R$ - APRES   
2                                KSB ELETRONICA LTDA  COMPRA A/V - R$ - APRES   
3                                      NAO SE APLICA        SAQUE CASH/ATM BB   
4                                      NAO SE APLICA        SAQUE CASH/ATM BB   

  DATA TRANSAÇÃO  VALOR TRANSAÇÃO  
0     08/12/2021             40.6  
1     01/12/2021            225.0  
2     16/12/2021            589.0  
3     06/12/2021            360.0  
4     25/11/2021             90.0


 Informações gerais
<class 'pandas.DataFrame'>
RangeIndex: 411652 entries, 0 to 411651
Data columns (total 15 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   CÓDIGO ÓRGÃO SUPERIOR   411652 non-null  int64  
 1   NOME ÓRGÃO SUPERIOR     411652 non-null  str    
 2   CÓDIGO ÓRGÃO            411652 non-null  int64  
 3   NOME ÓRGÃO              411652 non-null  str    
 4   CÓDIGO UNIDADE GESTORA  411652 non-null  int64  
 5   NOME UNIDADE GESTORA    411652 non-null  str    
 6   ANO EXTRATO             411652 non-null  int64  
 7   MÊS EXTRATO             411652 non-null  int64  
 8   CPF PORTADOR            312122 non-null  str    
 9   NOME PORTADOR           411652 non-null  str    
 10  CNPJ OU CPF FAVORECIDO  411652 non-null  int64  
 11  NOME FAVORECIDO         411652 non-null  str    
 12  TRANSAÇÃO               411652 non-null  str    
 13  DATA TRANSAÇÃO          312122 non-null  str    
 14  VALOR TRAN

CÓDIGO ÓRGÃO SUPERIOR       int64
NOME ÓRGÃO SUPERIOR           str
CÓDIGO ÓRGÃO                int64
NOME ÓRGÃO                    str
CÓDIGO UNIDADE GESTORA      int64
NOME UNIDADE GESTORA          str
ANO EXTRATO                 int64
MÊS EXTRATO                 int64
CPF PORTADOR                  str
NOME PORTADOR                 str
CNPJ OU CPF FAVORECIDO      int64
NOME FAVORECIDO               str
TRANSAÇÃO                     str
DATA TRANSAÇÃO                str
VALOR TRANSAÇÃO           float64
dtype: object

In [8]:
df['VALOR TRANSAÇÃO'] = pd.to_numeric(df['VALOR TRANSAÇÃO'], errors='coerce')

In [9]:
# --- 2.3 Estatísticas descritivas ---
print(' Estatísticas descritivas (atributos numéricos) ')
display(df.describe())

print('\n Estatísticas descritivas (atributos categóricos) ')
display(df.describe(include='object'))

 Estatísticas descritivas (atributos numéricos) 


CÓDIGO ÓRGÃO SUPERIOR   CÓDIGO ÓRGÃO  CÓDIGO UNIDADE GESTORA  \
count          411652.000000  411652.000000           411652.000000   
mean            35787.258318   30911.044040           193672.907524   
std             11399.429079   10231.341767           116415.455532   
min             20000.000000   20101.000000           110001.000000   
25%             26000.000000   25205.000000           114625.000000   
50%             30000.000000   26409.000000           160160.000000   
75%             47000.000000   30108.000000           200364.000000   
max             81000.000000   81000.000000           888310.000000   

         ANO EXTRATO    MÊS EXTRATO  CNPJ OU CPF FAVORECIDO  VALOR TRANSAÇÃO  
count  411652.000000  411652.000000            4.116520e+05    411652.000000  
mean     2023.010757       7.436845            1.456817e+13       683.603481  
std         0.821223       3.267999            2.231868e+13      2164.235331  
min      2022.000000       1.000000           -1.100000e+01         0.040000  
25%      2022.000000       5.000000           -2.000000e+00       125.000000  
50%      2023.000000       8.000000            4.006471e+12       356.710000  
75%      2024.000000      10.000000            2.069923e+13      1000.000000  
max      2024.000000      12.000000            9.874986e+13    207953.600000


 Estatísticas descritivas (atributos categóricos) 


NOME ÓRGÃO SUPERIOR       NOME ÓRGÃO  \
count                                      411652           411652   
unique                                         30              194   
top     Ministério da Justiça e Segurança Pública  Polícia Federal   
freq                                        83599            79609   

                                 NOME UNIDADE GESTORA    CPF PORTADOR  \
count                                          411652          312122   
unique                                           1255            9883   
top     COORDENACAO GERAL DE ADMINISTRACAO CGAD/DLOG/  ***.735.900-**   
freq                                            21527            1071   

       NOME PORTADOR NOME FAVORECIDO                TRANSAÇÃO DATA TRANSAÇÃO  
count         411652          411652                   411652         312122  
unique          9932           60321                        8           1091  
top         Sigiloso        Sigiloso  COMPRA A/V - R$ - APRES     22/11/2024  
freq           99530           99530                   265854            845

In [10]:
# --- 2.4 Visualizações exploratórias ---

import plotly.express as px
fig = px.violin(df, x="ANO EXTRATO", y="VALOR TRANSAÇÃO", box=True)

fig.update_layout(
    width=1000,
    height=600,
    template="plotly_white",
    xaxis_title="ANO EXTRATO",
    yaxis_title="VALOR TRANSAÇÃO (R$)",
)

fig.show()

---

## 3. Qualidade dos Dados

Os principais problemas tratados nesta etapa são:

#### 3.1. Tratamento de Ausência de Valores

Valores ausentes podem surgir por falhas de coleta ou campos opcionais.
A estratégia padrão inclui eliminar as linhas com valores ausentes em atributos críticos.
a principio, nao eliminamos pois nao usaremos as colunas que contem dados nulos no modelo.

(*discutir depois aula 2 qualidade dos dados)

#### 3.2 Tratamento de Ruído e Dados Inconsistentes

Para objetos, ruído é um objeto estranho.
Para atributos, ruído refere-se à modificação dos valores originais.
entendemos que ruído pode confundir o algoritmo.

(verificar se saque pode ser um ruido)

In [ ]:
# --- 3.2 Análise de valores ausentes ---
print('Valores ausentes por coluna')
df.isna().sum()

In [ ]:
# --- 3.3 Tratamento de valores ausentes ---

# Estratégia 1: Eliminar colunas com mais de X% de nulos
LIMIAR_NULOS = 70  # percentual
colunas_excluir = resumo_nulos[resumo_nulos['% do Total'] > LIMIAR_NULOS].index.tolist()
print(f'Colunas removidas (> {LIMIAR_NULOS}% nulos): {colunas_excluir}')
df.drop(columns=colunas_excluir, inplace=True, errors='ignore')

# Estratégia 2: Para colunas numéricas restantes, imputar com mediana
cols_numericas = df.select_dtypes(include=[np.number]).columns
for col in cols_numericas:
    if df[col].isnull().sum() > 0:
        mediana = df[col].median()
        df[col].fillna(mediana, inplace=True)
        print(f'  Coluna "{col}": nulos imputados com mediana = {mediana:.2f}')

# Estratégia 3: Para colunas categóricas, imputar com moda ou 'DESCONHECIDO'
cols_categoricas = df.select_dtypes(include='object').columns
for col in cols_categoricas:
    if df[col].isnull().sum() > 0:
        df[col].fillna('DESCONHECIDO', inplace=True)
        print(f'  Coluna "{col}": nulos preenchidos com "DESCONHECIDO"')

print(f'\nValores ausentes restantes: {df.isnull().sum().sum()}')

In [ ]:
# --- 3.4 Remoção de ruído e dados inconsistentes ---

# TODO: Ajustar conforme as colunas reais do CSV
# Exemplo: remover transações com valor = 0 (sem significado)
# col_valor = 'VALOR_TRANSACAO'
# n_antes = len(df)
# df = df[df[col_valor] != 0]
# print(f'Registros com valor 0 removidos: {n_antes - len(df)}')

# Nota: Valores negativos podem representar estornos legítimos ou erros.
# Avaliar e documentar a decisão:
# n_negativos = (df[col_valor] < 0).sum()
# print(f'Transações com valor negativo: {n_negativos}')
# Decisão: manter valores negativos para análise ou remover como ruído?

print('Etapa de remoção de ruído concluída.')
print(f'Shape atual do DataFrame: {df.shape}')

#### 3.5 Verificação de Duplicatas

Verificação de registros duplicados na base de dados conforme solicitado.

In [ ]:
# --- 3.5 Verificação de duplicatas ---
df[df.duplicated()]
print("Total de linhas:", len(df))
print("Duplicadas:", df.duplicated().sum())
df[df.duplicated(keep=False)].head()

---

## 4. Agregação dos Dados

### 4.1 Fundamentação

Nesta etapa, criamos um novo dataframe agrupando os dados por CPF do portador do cartão. O objetivo é transformar os dados  em um
perfil de comportamento por portador do cartão, bisando que os algoritmos de mineração identifiquem padrões e anomalias do usuário.


In [ ]:
# --- 4.2 Agregação por CPF do portador ---

df_servidor = (
    df.groupby('CPF PORTADOR')
      .agg(
          total_gasto=('VALOR TRANSAÇÃO', 'sum'),
          media_gasto=('VALOR TRANSAÇÃO', 'mean'),
          qtd_transacoes=('VALOR TRANSAÇÃO', 'count'),
          max_gasto=('VALOR TRANSAÇÃO', 'max')
      )
      .reset_index()
)

In [ ]:
df_servidor.head()

---

## 5. Transformação dos Dados
### 5.1 Normalização

Técnicas comuns de normalização:

- **Min-Max Scaling:** Transforma os valores para o intervalo [0, 1].
- **Z-Score (Standardization):** Centraliza na média 0 e desvio padrão 1.

Utilizaremos StandardScaler (Z-Score) neste projeto, pois é mais robusto
na presença de outliers que a normalização Min-Max.

In [ ]:
from sklearn.preprocessing import StandardScaler

features = ['total_gasto', 'media_gasto', 'qtd_transacoes', 'max_gasto']

scaler = StandardScaler()
X_scaled = scaler.fit_transform(df_servidor[features])

In [ ]:
df_scaled = pd.DataFrame(
    X_scaled,
    columns=features,
    index=df_servidor.index
)

In [ ]:
df_scaled.head()

---

## 6. Exportação dos Dados Pré-processados

O DataFrame limpo e normalizado é salvo para ser consumido pelo Notebook 02 (Mineração).

In [ ]:
# --- 6.1 Salvar dados processados ---
OUTPUT_DIR = os.path.join('..', 'dados')
# Para Colab:
# OUTPUT_DIR = '/content/drive/MyDrive/cpgf-anomaly-detection/dados'

# DataFrame original limpo (sem normalização) — para análise qualitativa no Notebook 03
df.to_csv(os.path.join(OUTPUT_DIR, 'cpgf_limpo.csv'), index=False, sep=';', encoding='utf-8')
print('Arquivo salvo: cpgf_limpo.csv')

# DataFrame normalizado — para entrada nos algoritmos de agrupamento
df_normalizado.to_csv(os.path.join(OUTPUT_DIR, 'cpgf_normalizado.csv'), index=False, sep=';', encoding='utf-8')
print('Arquivo salvo: cpgf_normalizado.csv')

print(f'\nShape final: {df_normalizado.shape}')
print('\n✅ Pré-processamento concluído com sucesso!')